---

# S03E05 : Fonctions & décorateurs - Décorateurs basiques

Cyril Desjouy

---


## 1. Introduction

Les décorateurs sont une partie importante de Python. Ce sont des fonctions modifiant le fonctionnement d'autres fonctions. Ils permettent d'écrire du code plus concis et élégant. 

Nous avons vu précédemment qu'il est possible de définir une fonction dans une fonction (***nested functions***) et qu'une fonction peut elle même retourner une fonction (***factory function***). Ce sont ces concepts qui sont utilisés pour l'implémentation des décorateurs sous Python.

<div class="alert alert-block alert-info">
Commençons par l'exemple suivant:
</div>

In [ ]:
# The decorator
def prettier(func):
    def wrapper():
        print('.oOO Processing OOo.'.center(80))
        func()
        print('.oOO ~~~Done~~~ OOo.'.center(80))
    return wrapper

# The function to decorate
def stuff():
    print('Doing some stuff'.center(80))

print('Call stuff:')
stuff()

print('\nDecorate stuff and call it:')
pretty = prettier(stuff)
pretty()

Le decorateur `prettier` enferme une fonction imbriquée qu'on appelle généralement `wrapper`. Cette fonction `wrapper` *enveloppe* en effet la fonction à décorer dans un nouveau contexte.

Afin de décorer la fonction `stuff`, il suffit de créer une nouvelle fonction à l'aide de la ***factory function*** `prettier` et de réassigner ce résultat à un nouvel identifieur `pretty`.

L'utilisation des décorateurs étant très courante sous Python, une syntaxe simplifié a été proposée. Il suffit de placer le symbole `@` avec le nom du décorateur au dessus de la définition de la fonction comme suit:

In [ ]:
@prettier
def stuff():
    print('Doing some stuff'.center(80))
    
stuff()

Voilà! Ceci présente le principe de base des décorateurs.

## 2. Fonctions avec arguments

Si on souhaite utiliser notre décorateur `prettier` sur une fonction prenant des argument d'entrée comme par exemple:

In [ ]:
@prettier
def stuff(task, like_a=''):
    print(f'Doing {task} like a {like_a}'.center(80))
    
stuff('some tidying up', like_a='turtle')

l'appel de la fonction `stuff` lève alors une exception! En effet, la fonction imbriquée `wrapper` n'accepte pas d'arguments d'entrée. Il s'agit donc de la modifier afin qu'elle accepte les arguments `task` et `like_a` comme suit:

In [ ]:
def prettier(func):
    def wrapper(task, like_a):
        print('.oOO Processing OOo.'.center(80))
        func(task, like_a)
        print('.oOO ~~~Done~~~ OOo.'.center(80))
    return wrapper
    
@prettier
def stuff(task, like_a=''):
    print(f'Doing {task} like a {like_a}'.center(80))

stuff('some tidying up', like_a='turtle')

Cela fonctionne très bien, mais l'utilisation de notre décorateur est maintenant limitée à des fonctions prenant exclusivement deux arguments d'entrée. La décoration de la fonction `other_stuff` suivante lève par exemple une exception.
```python
@prettier
def other_stuff(task):
    print(f'Doing {task}'.center(80))
    
>> other_stuff('maths')
TypeError: decorate() missing 1 required positional argument: 'like_a'
```

Nous avons vu précédemment l'utilisation des `*args/**kwargs` pour définir une fonction avec un nombre d'arguments arbitraire. Cela n'aura pas servi à rien puisqu'il vont nous être très utiles ici.

<div class="alert alert-block alert-info">
Testez l'exemple suivant:
</div>

In [ ]:
def prettier(func):
    def wrapper(*args, **kwargs):
        print('.oOO Processing OOo.'.center(80))
        func(*args, **kwargs)
        print('.oOO ~~~Done~~~ OOo.'.center(80))
    return wrapper

@prettier
def stuff(task, like_a=''):
    print(f'Doing {task} like a {like_a}'.center(80))
    
@prettier
def more_stuff(task1, task2, like_a=''):
    print(f'Doing {task1} and {task2} like a {like_a}'.center(80))

print('Call stuff:')
stuff('Python', 'boss')

print('\nCall more_stuff:')
more_stuff('maths', 'physics', like_a='mad')

Notre décorateur est maintenant polyvalent. Il peut être utilisé sur n'importe quelle fonction!

## 3. Retourner des valeurs depuis un décorateur

Observons maintenant ce qui se passe lorsque la fonction à décorer retourne une valeur:

In [ ]:
@prettier
def stuff(task, like_a=''):
    return f'Doing {task} like a {like_a}'.center(20)

result = stuff('math', 'boss')         # result is None!
print(result)

Lorque le décorateur précédemment développé est appliqué à la nouvelle fonction `prettier`, tout semble *cassé*. La fonction `stuff` décorée ne retourne en effet plus rien. Rappelons que décorer une fonction revient à écrire : 
```python
pretty = prettier(stuff)
pretty()
```
La fonction `prettier` retourne `wrapper` qui est alors référencé par `pretty`. Or la fonction `wrapper` (ou `pretty`) ne retourne rien ! Il est alors normal que notre fonction décorée ne retourne rien. 
Pour que `wrapper` retourne une valeur, il faut bien sûr implémenter explicitement l'instruction `return`:

In [ ]:
def prettier(func):
    def wrapper(*args, **kwargs):
        result = func(*args, **kwargs)
        print('.oOO Processing OOo.'.center(80))
        print(result)
        print('.oOO ~~~Done~~~ OOo.'.center(80))
        return result                            # Return func(*args, **kwargs)
    return wrapper

@prettier
def stuff(task, like_a=''):
    return f'Doing {task} like a {like_a}'.center(80)

print('Call stuff:')
result = stuff('math', 'boss')
print('\nPrint result:')
print(result)

## 4. Empiler les décorateurs

Il est tout à fait possible d'appliquer plusieurs décorateurs à une fonction. Il suffit pour cela de les empiler comme ceci:

In [ ]:
def stars(func):
    def wrapper(*args, **kwargs):
        print((30*'*').center(80))
        func(*args, **kwargs)
        print((30*'*').center(80))
    return wrapper

def repeat(func):
    def wrapper(*args, **kwargs):
        func(*args, **kwargs)
        func(*args, **kwargs)
    return wrapper

@stars
@repeat
def stuff(task, like_a=''):
    print(f'Doing {task} like a {like_a}'.center(80))

    
stuff('Python', like_a='boss')

<div class="alert alert-block alert-info">
Inversez les deux décorateurs et concluez.
</div>

## Application: Timing


<div class="alert alert-block alert-info">
Utiliser la fonction <code>perf_counter</code> du module <code>time</code> afin d'implémenter un décorateur <code>timing</code> fonctionnant comme suit:
</div>

```python
@timing
def mult(x, y):
    return x*y

@timing
def div(x, y):
    return x/y

m = mult(2, 4)
d = div(2, 4)

print(f'\nResult of multiplication: {m}')
print(f'Result of division: {d}')
```

<div class="alert alert-block alert-info">
Cette série d'instructions retournera :
</div>

```python
mult executed in 3.57e-06 s
div executed in 4.82e-06 s

Result of multiplication: 8
Result of division: 0.5
```

**Note:** *Pour accéder au nom d'une fonction vous pouvez utiliser son attribut `__name__`.*